### importing necessary libraries 

In [1]:
import numpy as np

import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json

!pip -q install  geopy  
from geopy.geocoders import Nominatim

import requests
from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans
!pip -q install folium  
import folium

print('Libraries Imported!')

Libraries Imported!


In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


### Dealing with json data to obtain the Dataframe

In [3]:

with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:

newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [5]:
NY_neighborhoods_data = newyork_data['features']

In [6]:
NY_neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [7]:
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude']

NY_neighborhoods = pd.DataFrame(columns = column_names)

In [8]:
NY_neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [9]:
for data in NY_neighborhoods_data:
    borough = data['properties']['borough']
    neighborhood_name = data['properties']['name']
    
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    NY_neighborhoods = NY_neighborhoods.append({'Borough': borough,
                                               'Neighborhood': neighborhood_name,
                                               'Latitude': neighborhood_lat,
                                               'Longitude': neighborhood_lon}, ignore_index = True)

In [10]:
NY_neighborhoods.head()
NY_neighborhoods.to_excel(r"IBM_NY_data.xlsx")

In [11]:

print('The Dataframe has {} boroughs and {} neighborhoods.'.format(
        len(NY_neighborhoods['Borough'].unique()),
        NY_neighborhoods.shape[0]
))

The Dataframe has 5 boroughs and 306 neighborhoods.


In [12]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent = 'ny_explorer')
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geographical coordinate of New York City are {} {}.'.format(latitude, longitude))

The geographical coordinate of New York City are 40.7127281 -74.0060152.


In [13]:
map_newyork = folium.Map(location = [latitude, longitude], zoom_start = 10)

for lat, lng, borough, neighborhood in zip(NY_neighborhoods['Latitude'], NY_neighborhoods['Longitude'], NY_neighborhoods['Borough'], NY_neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html = True)
    folium.CircleMarker(
        [lat, lng],
        radius = 5,
        popup = label,
        color = 'blue',
        fill = True,
        fill_color = '#3186cc',
        fill_opacity = 0.7,
        parse_html = False).add_to(map_newyork)

map_newyork

In [14]:
CLIENT_ID = 'HTEI3RFH5DTZHU5XWNSE4BIQYPMNB1MDNXPID3O04K303IQV' # your Foursquare ID
CLIENT_SECRET = 'SUYEQBXTGB4QKND0IYAWYMQUXDR451LPGQQAR1PEWATXQQC5' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: HTEI3RFH5DTZHU5XWNSE4BIQYPMNB1MDNXPID3O04K303IQV
CLIENT_SECRET:SUYEQBXTGB4QKND0IYAWYMQUXDR451LPGQQAR1PEWATXQQC5


In [15]:
LIMIT = 100
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [16]:
NY_venues = getNearbyVenues(names = NY_neighborhoods['Neighborhood'], latitudes = NY_neighborhoods['Latitude'], longitudes = NY_neighborhoods['Longitude'])

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [17]:
print(NY_venues.shape)
NY_venues.head()

(10097, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3         Walgreens       40.896528       -73.844700        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [18]:
NY_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      30                      30   
Annadale                                      11                      11   
Arden Heights                                  5                       5   
Arlington                                      6                       6   
Arrochar                                      21                      21   
Arverne                                       20                      20   
Astoria                                       99                      99   
Astoria Heights                               13                      13   
Auburndale                                    20                      20   
Bath Beach                                    46                      46   
Battery Park City                             66                      66   
Bay Ridge                                     81                      81   
Bay Terrace                                   47                      47   
Baychester                                    20                      20   
Bayside                                       71                      71   
Bayswater                                      1                       1   
Bedford Park                                  36                      36   
Bedford Stuyvesant                            28                      28   
Beechhurst                                    16                      16   
Bellaire                                      13                      13   
Belle Harbor                                  17                      17   
Bellerose                                     19                      19   
Belmont                                       97                      97   
Bensonhurst                                   36                      36   
Bergen Beach                                   7                       7   
Blissville                                    19                      19   
Bloomfield                                     4                       4   
Boerum Hill                                   90                      90   
Borough Park                                  22                      22   
Breezy Point                                   5                       5   
Briarwood                                     10                      10   
Brighton Beach                                43                      43   
Broad Channel                                  5                       5   
Broadway Junction                             20                      20   
Bronxdale                                     14                      14   
Brooklyn Heights                             100                     100   
Brookville                                     2                       2   
Brownsville                                   16                      16   
Bulls Head                                    45                      45   
Bushwick                                      69                      69   
Butler Manor                                   4                       4   
Cambria Heights                               11                      11   
Canarsie                                       6                       6   
Carnegie Hill                                 86                      86   
Carroll Gardens                              100                     100   
Castle Hill                                    8                       8   
Castleton Corners                             14                      14   
Central Harlem                                45                      45   
Charleston                                    27                      27   
Chelsea                                      106                     106   
Chinatown                                    100                     100   

In [19]:
print('There are {} unique categories.'.format(len(NY_venues['Venue Category'].unique())))

There are 428 unique categories.


In [25]:
NY_onehot = pd.get_dummies(NY_venues[['Venue Category']], prefix = "", prefix_sep = "")

NY_onehot['Neighborhood'] = NY_venues['Neighborhood']

col_list = list(NY_onehot.columns)
col_list.remove('Neighborhood')
cols = ['Neighborhood'] + [col for col in col_list]

NY_onehot = NY_onehot[cols]

NY_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0    Wakefield                  0               0                  0   
1    Wakefield                  0               0                  0   
2    Wakefield                  0               0                  0   
3    Wakefield                  0               0                  0   
4    Wakefield                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                   0                 0                    0             0   
1                   0                 0                    0             0   
2                   0                 0                    0             0   
3                   0                 0                    0             0   
4                   0                 0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Garage  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0                0          0           0           0       0   
1            0                0          0           0           0       0   
2            0                0          0           0           0       0   
3            0                0          0           0           0       0   
4            0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0     0    0               0                 0                 0           0   
1     0    0               0                 0                 0           0   
2     0    0               0                 0                 0           0   
3     0    0               0                 0                 0           0   
4     0    0               0                 0                 0           0   

   Beach  Beach Bar  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0      0          0         0            0           0              0   
1      0          0         0            0           0              0   
2      0          0         0            0           0              0   
3      0          0         0            0           0              0   
4      0          0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0

In [26]:
NY_onehot.shape

(10097, 428)

In [27]:
NY_grouped = NY_onehot.groupby('Neighborhood').mean().reset_index()
NY_grouped

Neighborhood  Accessories Store  Adult Boutique  \
0                     Allerton           0.000000            0.00   
1                     Annadale           0.000000            0.00   
2                Arden Heights           0.000000            0.00   
3                    Arlington           0.000000            0.00   
4                     Arrochar           0.000000            0.00   
5                      Arverne           0.000000            0.00   
6                      Astoria           0.000000            0.00   
7              Astoria Heights           0.000000            0.00   
8                   Auburndale           0.000000            0.00   
9                   Bath Beach           0.000000            0.00   
10           Battery Park City           0.000000            0.00   
11                   Bay Ridge           0.000000            0.00   
12                 Bay Terrace           0.021277            0.00   
13                  Baychester           0.000000            0.00   
14                     Bayside           0.000000            0.00   
15                   Bayswater           0.000000            0.00   
16                Bedford Park           0.000000            0.00   
17          Bedford Stuyvesant           0.000000            0.00   
18                  Beechhurst           0.000000            0.00   
19                    Bellaire           0.000000            0.00   
20                Belle Harbor           0.000000            0.00   
21                   Bellerose           0.000000            0.00   
22                     Belmont           0.000000            0.00   
23                 Bensonhurst           0.000000            0.00   
24                Bergen Beach           0.000000            0.00   
25                  Blissville           0.000000            0.00   
26                  Bloomfield           0.000000            0.00   
27                 Boerum Hill           0.000000            0.00   
28                Borough Park           0.000000            0.00   
29                Breezy Point           0.000000            0.00   
30                   Briarwood           0.000000            0.00   
31              Brighton Beach           0.000000            0.00   
32               Broad Channel           0.000000            0.00   
33           Broadway Junction           0.000000            0.00   
34                   Bronxdale           0.000000            0.00   
35            Brooklyn Heights           0.000000            0.00   
36                  Brookville           0.000000            0.00   
37                 Brownsville           0.000000            0.00   
38                  Bulls Head           0.000000            0.00   
39                    Bushwick           0.000000            0.00   
40                Butler Manor           0.000000            0.00   
41             Cambria Heights           0.000000            0.00   
42                    Canarsie           0.000000            0.00   
43               Carnegie Hill           0.000000            0.00   
44             Carroll Gardens           0.000000            0.00   
45                 Castle Hill           0.000000            0.00   
46           Castleton Corners           0.000000            0.00   
47              Central Harlem           0.000000            0.00   
48                  Charleston           0.000000            0.00   
49                     Chelsea           0.000000            0.00   
50                   Chinatown           0.000000            0.00   
51                 City Island           0.000000            0.00   
52                   City Line           0.000000            0.00   
53                Civic Center           0.000000            0.00   
54           Claremont Village           0.000000            0.00   
55                Clason Point           0.000000            0.00   
56                     Clifton           0.000000            0.00   
57              

In [28]:
NY_grouped.shape

(302, 428)

In [29]:
export_excel = NY_grouped.to_excel(r"IBM_NY_grouped.xlsx")